In [ ]:
#Folium Test Program
# To install folium to your computer run the following 
# conda install --channel https://conda.anaconda.org/conda-forge folium


In [261]:
import src.folium.folium.folium
import pandas as pd
import numpy as np
from datetime import datetime

ImportError: No module named src.folium.folium.folium

In [260]:
map_osm = folium.Map(location=[37.79086, -122.40147], zoom_start=14)
folium.Marker([37.79086, -122.40147], popup='General Assembly'
              ).add_to(map_osm)
#map_osm.save('osm.html')
map_osm

In [3]:
state_geo = 'us-states.json'
state_unemployment = (
    r'https://raw.githubusercontent.com/python-visualization/folium/master/examples/US_Unemployment_Oct2012.csv')

state_data = pd.read_csv(state_unemployment)

state_data.head()

# To view json go to the following link:
# https://raw.githubusercontent.com/python-visualization/folium/master/examples/us-states.json

State  Unemployment
0    AL           7.1
1    AK           6.8
2    AZ           8.1
3    AR           7.2
4    CA          10.1

In [4]:
#Let Folium determine the scale and view Choropleth
states = folium.Map(location=[40, -102], zoom_start=4)
states.choropleth(geo_path=state_geo, data=state_data,
                columns=['State', 'Unemployment'],
                key_on='feature.id',
                fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Unemployment Rate (%)')

states

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:7: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


Lets start with a more local version 

A topic near and dear to my heart, 
human feces in San Francisco

View this map published by the amazing William Mees. https://willyem.carto.com/viz/156b1e0c-5b45-11e5-9351-0e018d66dc29/public_map

http://www.citylab.com/housing/2015/10/mapping-san-franciscos-sidewalk-pooping-problem/409561/

My plan for this exercise is to import 
in the GeoJson file for human feces over the last few years 
in San Francisco, as a way to visualize how the data is spread out over the years.

I will also be using a San Francisco geojson map of neighborhoods, and combining this with a dataset of excrement sightings to visualize it as an aggregate of data per neighborhood.

I will first just show a simple map of the points shown in the data set that William gathered. 

In [5]:
import json
with open('visualization_lecture/human_waste_data.geojson') as poop_file:
    poop_data = json.load(poop_file)

In [6]:
# Let's look at the first poop instance!
poop_data['features'][0]

{u'geometry': {u'coordinates': [-122.414495, 37.769535], u'type': u'Point'},
 u'properties': {u'address': u'Intersection of 13TH ST and TRAINOR ST',
  u'cartodb_id': 12980,
  u'caseid': 3744148,
  u'category': u'Street and Sidewalk Cleaning',
  u'closed': u'',
  u'field_1': 12979,
  u'lat': 37.769535428,
  u'lon': -122.414494983,
  u'neighborhood': u'Mission',
  u'opened': u'2014-06-16T08:41:07Z',
  u'point': u'(37.769535428, -122.414494983)',
  u'request_details': u'Human_waste_or_urine',
  u'request_type': u'Sidewalk_Cleaning',
  u'responsible_agency': u'DPW Ops Queue',
  u'source': u'Open311',
  u'status': u'Open',
  u'supervisor_district': 9,
  u'updated': u'06/16/2014 10:06:57 AM'},
 u'type': u'Feature'}

In [7]:
# OH MAN it happened in 2014!, lets section out this data, 
# for now I'll grab data from 2009.

def grab_year(poop_data, year, month):
    """Use Pandas to do this later"""
    rs = []
    start = datetime(year, month,1)
    end = datetime(year, month+1,1)
    for x in poop_data['features']:
        poop_date = datetime.strptime(x['properties']['opened'], '%Y-%m-%dT%H:%M:%SZ')
        if start <= poop_date < end:
            rs.append(x)
    return rs

def create_geojson_file(data, filename):
    """Create geojson file for poop data"""
    output = {}
    output["type"] = "FeatureCollection"
    output["features"] = data
    with open(filename, 'w') as outfile:
        json.dump(output, outfile)

def read_geojson_file(filename):
    with open(filename, 'r') as infile:
        return json.load(infile)

geo_path = 'visualization_lecture/2009_poop.json'
rs_2009 = grab_year(poop_data, 2009, 1)
create_geojson_file(rs_2009, geo_path)

In [53]:
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=geo_path)
poop_map

In [54]:
#Lets overlay that with some neighborhood break downs.
# I took this data from code america. Thanks Code America!
# https://github.com/codeforamerica/click_that_hood/blob/master/public/data/san-francisco.geojson

sf_path='visualization_lecture/san-francisco.geojson'
hood_json = read_geojson_file(sf_path)

#Add style attributes
my_style = {
    "color": "#ff7800",
    "weight": 2,
    "opacity": 0.65
}
folium.GeoJson(hood_json,
               style_function=lambda x: my_style, overlay=True).add_to(poop_map)

poop_map

In [10]:
# Okay, so this looks still funky. But its got some good information on it, 
# so lets try and aggregate all this data together using pandas!

#first lets read it into a dataframe and get the details we need from it
rs_2009[0]



{u'geometry': {u'coordinates': [-122.420202, 37.789322], u'type': u'Point'},
 u'properties': {u'address': u'1338 POLK ST, SAN FRANCISCO, CA, 94109',
  u'cartodb_id': 48355,
  u'caseid': 347563,
  u'category': u'Street and Sidewalk Cleaning',
  u'closed': u'01/29/2009 09:09:47 AM',
  u'field_1': 48354,
  u'lat': 37.789322012,
  u'lon': -122.420202321,
  u'neighborhood': u'Nob Hill',
  u'opened': u'2009-01-08T17:04:22Z',
  u'point': u'(37.789322012, -122.420202321)',
  u'request_details': u'Human_waste_or_urine',
  u'request_type': u'Sidewalk_Cleaning',
  u'responsible_agency': u'DPW Ops Queue',
  u'source': u'Voice In',
  u'status': u'Closed',
  u'supervisor_district': 3,
  u'updated': u'01/29/2009 09:09:47 AM'},
 u'type': u'Feature'}

In [152]:
# Seems like we will want the point, the date it was opened, the casid, 
# the neighborhood, and the supervisor_district, that could be interesting!
def get_details(item):
    details = {}
    details['point'] = item['geometry']['coordinates']
    details['date_opened'] = item['properties']['opened']
    details['caseid'] = item['properties']['caseid']
    details['neighborhood'] = item['properties']['neighborhood']
    details['supervisor_district'] = item['properties']['supervisor_district']
    return details

rs = []
for incident in poop_data['features']:
    rs.append(get_details(incident))
poop_frame = pd.DataFrame(rs)
poop_frame.head()

caseid         date_opened     neighborhood                     point  \
0  3744148 2014-06-16 08:41:07          Mission  [-122.414495, 37.769535]   
1  4883104 2015-07-06 00:15:27       Polk Gulch  [-122.422226, 37.791133]   
2  4973692 2015-08-06 14:51:09       Tenderloin    [-122.41429, 37.78327]   
3  4877314 2015-07-02 23:58:02        Japantown  [-122.433326, 37.787079]   
4  4852002 2015-06-24 12:39:26  South of Market  [-122.414121, 37.778165]   

   supervisor_district  
0                    9  
1                    3  
2                    6  
3                    5  
4                    6

In [265]:
print len(poop_frame.groupby(['neighborhood']).count())
len(hood_json['features'])

115


37

In [155]:
# K so it seems like we have a much bigger amount of neighborhoods in the incident data,
# than in our neighborhood layer. 
# lets try and match each incident to the existing neighborhood layer we got.
# For that we will use the shapely library we just downloaded.
import shapely.geometry
point = shapely.geometry.Point (poop_frame.point[0])
print datetime.now()

2016-07-31 14:43:12.181229


In [266]:
print datetime.now()
hood_shapes = []

for feature in hood_json["features"]:
    hood_shapes.append({
            "shape" : shapely.geometry.shape(feature["geometry"]),
             "name" : feature['properties']['name']})
    

poop_frame['shape_neighborhood'] = None
for hood_shape in hood_shapes:
    for row in poop_frame.loc[poop_frame['shape_neighborhood'].isnull(),:].itertuples():
        point = shapely.geometry.Point(row.point)
        # This will check to see if the incident was in the neighborhood
        if hood_shape['shape'].contains(point):
            poop_frame.loc[row[0], 'shape_neighborhood'] = hood_shape['name']

2016-08-01 23:00:25.921363


In [157]:
# Ok so now that we know how to match a poop spot with our existing neighborhood geojson file,
# lets make a new dataframe that has all the neighborhoods with their frequency per neighborhood 
all_years = poop_frame.groupby(['shape_neighborhood']).count()
all_years['shape_neighborhood'] = all_years.index

In [158]:
# Now lets associate it with our original neighborhood map.
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
sf_counties = 'visualization_lecture/san-francisco.geojson'
poop_map.choropleth(geo_path=sf_counties,
                    data=all_years,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [276]:
# We can see the automated legend is thrown off by the outliers, lets send in our own legend
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
sf_counties = 'visualization_lecture/san-francisco.geojson'
poop_map.choropleth(geo_path=sf_counties, data=exclude_downtown,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                threshold_scale=[2,200,400,1000],
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

In [279]:
def get_year(start_date, end_date, frame):
    df = frame.groupby(['shape_neighborhood']).count()
    df.caseid = 0
    date_frame = frame[(frame.date_opened >= start_date) &
                       (frame.date_opened < end_date)]
    date_frame = date_frame.groupby(['shape_neighborhood']).count()['caseid']
    df.update(date_frame)
    df.caseid = df.caseid.astype(int)
    df['shape_neighborhood'] = df.index
    return df

In [280]:
# Lets try on a per year basis!
year_view = get_year('2009-01-01', '2010-01-01', poop_frame)
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
sf_counties = 'visualization_lecture/san-francisco.geojson'
poop_map.choropleth(geo_path=sf_counties,
                    data=year_view,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:13: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [207]:
#2010
date_frame = get_year("2008-01-01", "2009-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:19: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [208]:
date_frame = get_year("2010-01-01", "2011-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [210]:
date_frame = get_year("2011-01-01", "2012-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [211]:
date_frame = get_year("2012-01-01", "2013-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [258]:
def get_threshold_scale(frame, column):
    """Get Threshold scale for frame
    
    We will use a larger than normal range for the first 4 scales.
    In order to get some more separation for the tiles"""
    rs = []
    for i in np.linspace(0.01, 0.9, 6, endpoint=True):
        rs.append(frame[frame[column] >0][column].quantile(i))
    return rs


date_frame = get_year("2013-01-01", "2014-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                threshold_scale=(get_threshold_scale(date_frame, 'caseid')),
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map